In [3]:
import sits.SITS as sits
import sits.export as sits_export

from datetime import datetime

import vector files into geodataframe

In [4]:
import geopandas as gpd
import pandas as pd

in_vect = "france_barkbeetle_lite_single.geojson"
# import into gdf with sits
test_2154 = sits.Vec2gdf(in_vect)
# check epsg
test_2154.gdf.crs.to_epsg()

2154

In [5]:
# calculates the bounding box for each feature.
test_2154.set_bbox('gdf')
test_2154.bbox.crs.to_epsg()

2154

display geodataframes with folium

In [6]:
import folium

f = folium.Figure(height=400)
m = folium.Map(location=[55, 0], zoom_start=3).add_to(f)
test_2154.gdf.explore(m=m, height=400, color='green')
test_2154.bbox.explore(m=m, height=400)

In [7]:
# check uniaue values in field "scolyte1"
test_2154.bbox["scolyte1"].unique()

array(['I', 'R', 'V', 'S', 'C', 'X', 'G'], dtype=object)

manage projection of bboxes layer
- add field ('bbox_4326') of bbox in epsg 4326
- add field ('bbox_3035') of bbox in epsg 3035
- add field ('bbox_tuple') of bbox in epsg 4326 and 3035

In [12]:
test_process = test_2154.bbox.to_crs(4326)

test_process = pd.concat([test_process, test_process['geometry'].bounds], axis=1)
test_process['bbox_4326'] = test_process[['minx', 'miny', 'maxx', 'maxy']].values.tolist()

test_3035 = test_2154.bbox.to_crs(3035)
test_3035_bounds = pd.concat([test_3035, test_3035['geometry'].bounds], axis=1)
test_3035_bounds['bbox_3035'] = test_3035_bounds[['minx', 'miny', 'maxx', 'maxy']].values.tolist()

test_process = pd.concat([test_process, test_3035_bounds['bbox_3035']], axis=1)
test_process['bbox_tuple'] = test_process.apply(lambda row: (row['bbox_4326'], row['bbox_3035']), axis=1)

test_process.head()

organisme        date   source propriete type_peup ess_princ ess_secon  \
0       ONF  2019-06-25  Terrain       PUB         R       EPC       EPC   
1       ONF  2019-06-25  Terrain       PUB         R       EPC        NR   
2       DSF  2018-12-06  Terrain      PRIV         R       EPC        NR   
3       DSF  2018-12-06  Terrain      PRIV         R       EPC        NR   
4       DSF  2018-12-06  Terrain      PRIV         R       EPC        NR   

  pres_melez ess_touch1 scolyte1  ... struct_peup PLOT_ID_S  \
0          0        EPC        I  ...           R         1   
1         NR        EPC        R  ...           R         2   
2         NR        EPC        R  ...           R         3   
3         NR        EPC        V  ...           R         4   
4         NR         NR        S  ...           R         5   

                                            geometry      minx       miny  \
0  POLYGON ((2.82602 45.63494, 2.82602 45.63530, ...  2.825504  45.634941   
1  POLYGON ((6.13968 45.58716, 6.13969 45.58742, ...  6.139293  45.587155   
2  POLYGON ((5.53446 48.46721, 5.53449 48.46776, ...  5.534088  48.467213   
3  POLYGON ((5.53447 48.46654, 5.53450 48.46728, ...  5.534190  48.466543   
4  POLYGON ((5.54133 48.46731, 5.54137 48.46817, ...  5.540081  48.467306   

       maxx       maxy                                          bbox_4326  \
0  2.826019  45.635302  [2.8255044256228508, 45.634941277411386, 2.826...   
1  6.139693  45.587436  [6.139293359502604, 45.587155051477055, 6.1396...   
2  5.534491  48.467771  [5.534088480344151, 48.46721314992736, 5.53449...   
3  5.534504  48.467287  [5.534190109814471, 48.46654256305175, 5.53450...   
4  5.541369  48.468197  [5.540081457732796, 48.46730642585579, 5.54136...   

                                           bbox_3035  \
0  [3761787.7849638816, 2529437.8009796273, 37618...   
1  [4019438.9740521642, 2504995.883254013, 401947...   
2  [3990846.743521249, 2827079.0831763, 3990880.0...   
3  [3990849.826223296, 2827004.636245847, 3990877...   
4  [3991289.9031796386, 2827058.74595494, 3991390...   

                                          bbox_tuple  
0  ([2.8255044256228508, 45.634941277411386, 2.82...  
1  ([6.139293359502604, 45.587155051477055, 6.139...  
2  ([5.534088480344151, 48.46721314992736, 5.5344...  
3  ([5.534190109814471, 48.46654256305175, 5.5345...  
4  ([5.540081457732796, 48.46730642585579, 5.5413...  

[5 rows x 25 columns]

create function for loading sits and export to netcdf

In [15]:
def f_test(aoi_bounds_latlong, aoi_bounds_proj, gid, rep):
    # loads time-series images in EPSG:3035
    imgcoll = sits.StacAttack()
    imgcoll.searchItems(aoi_bounds_latlong, date_start=datetime(2023, 1, 1), date_end=datetime(2023, 12, 31))
    #imgcoll.loadImgs(aoi_bounds_proj, crs_out=3035)
    imgcoll.loadPatches(aoi_bounds_proj, dimx=10, dimy=10, crs_out=3035)
    # exports time-series into csv file and netCDF file
    imgcoll.to_nc(f"/eos/jeodpp/home/users/osekenj/data/temp_data/{rep}", gid, 'patch')

In [16]:
%%time

#test 01
for gid, i in enumerate(test_process['bbox_tuple'][:20]):
    f_test(i[0], i[1], gid, "test01_classic")

#CPU times: user 17min 23s, sys: 10min 45s, total: 28min 9s
#Wall time: 10min 26s

/home/osekenj/.local/lib/python3.11/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(


CPU times: user 15min 24s, sys: 10min 20s, total: 25min 44s
Wall time: 10min 12s


In [19]:
%%time
outdir = "/eos/jeodpp/home/users/osekenj/data/temp_data/test01_dask"
test = sits.Multiproc('patch', 'nc', outdir) # dask processes mode

geolayer = test_2154.gdf.to_crs(3035) #test_3035_gdf
id_field = 'PLOT_ID'
test.add_label(geolayer, id_field)

for gid, i in enumerate(test_process['bbox_tuple'][:20]):
    test.fetch_func(i[0], i[1], gid, dimx=10, dimy=10) #resolution=20
test.dask_compute()

#CPU times: user 83.9 ms, sys: 31.9 ms, total: 116 ms
#Wall time: 4min 21s

/home/osekenj/.local/lib/python3.11/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(
/home/osekenj/.local/lib/python3.11/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(
/home/osekenj/.local/lib/python3.11/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(
/home/osekenj/.local/lib/python3.11/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(
/home/osekenj/.local/lib/python3.11/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(
/home/osekenj/.local/lib/python3.11

CPU times: user 378 ms, sys: 46.8 ms, total: 424 ms
Wall time: 4min 28s


(None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None)

In [ ]:
"""
%%time
outdir = "/eos/jeodpp/home/users/<>/data/temp_data/test06_threads"
test = sits.Multiproc('patch', 'nc', outdir)
for gid, i in enumerate(test_process['bbox_tuple'][:20]):
    test.fetch_func(i[0], i[1], gid, dimx=10, dimy=10)
test.dask_compute(scheduler_type='threads')
"""
#CPU times: user 24min 39s, sys: 19min 37s, total: 44min 16s
#Wall time: 21min 38s

"""
%%time
outdir = "/eos/jeodpp/home/users/<>/data/temp_data/test06_distributed"
test = sits.Multiproc('patch', 'nc', outdir)
for gid, i in enumerate(test_process['bbox_tuple'][:20]):
    test.fetch_func(i[0], i[1], gid, dimx=10, dimy=10)
test.dask_compute(scheduler_type='distributed')
"""
#RuntimeError: Requested distributed scheduler but no Client active.

### open netcdf

In [18]:
import xarray as xr
#import os

array_subset = xr.open_dataset(
    os.path.join(outdir, 'S2_fid-0_patch_2023-01-01 00:00:00-2023-12-31 00:00:00.nc')
    )

array_subset

<xarray.Dataset> Size: 314kB
Dimensions:      (y: 10, x: 10, time: 142)
Coordinates:
  * y            (y) float64 80B 2.53e+06 2.529e+06 ... 2.529e+06 2.529e+06
  * x            (x) float64 80B 3.762e+06 3.762e+06 ... 3.762e+06 3.762e+06
  * time         (time) datetime64[ns] 1kB 2023-01-02T10:44:41.025000 ... 202...
Data variables:
    spatial_ref  int32 4B ...
    B02          (time, y, x) uint16 28kB ...
    B03          (time, y, x) uint16 28kB ...
    B04          (time, y, x) uint16 28kB ...
    B05          (time, y, x) uint16 28kB ...
    B06          (time, y, x) uint16 28kB ...
    B07          (time, y, x) uint16 28kB ...
    B08          (time, y, x) uint16 28kB ...
    B8A          (time, y, x) uint16 28kB ...
    B11          (time, y, x) uint16 28kB ...
    B12          (time, y, x) uint16 28kB ...
    SCL          (time, y, x) uint16 28kB ...

In [20]:
array_subset.B03

<xarray.DataArray 'B03' (time: 142, y: 10, x: 10)> Size: 28kB
[14200 values with dtype=uint16]
Coordinates:
  * y        (y) float64 80B 2.53e+06 2.529e+06 ... 2.529e+06 2.529e+06
  * x        (x) float64 80B 3.762e+06 3.762e+06 ... 3.762e+06 3.762e+06
  * time     (time) datetime64[ns] 1kB 2023-01-02T10:44:41.025000 ... 2023-12...
Attributes:
    nodata:        0
    grid_mapping:  spatial_ref

In [1]:
import sits.export as export
path = "/eos/jeodpp/home/users/osekenj/data/temp_data/test08/S2_fid-0_patch_2023-01-01 00:00:00-2023-12-31 00:00:00.nc"
test = export.Sits_ds(path)
test.ds2da()
test.export2gif(imgfile="/eos/jeodpp/home/users/osekenj/data/temp_data/test08/toto.gif")
test.gif


In [6]:
import sits.export as export
import geogif
import xarray as xr

In [16]:
ds = xr.open_dataset("/eos/jeodpp/home/users/osekenj/data/temp_data/test08/S2_fid-0_patch_2023-01-01 00:00:00-2023-12-31 00:00:00.nc", engine="netcdf4")


bands_to_keep = ['B04', 'B03', 'B02'] 
selected_ds = ds[bands_to_keep]

band_dataarray = selected_ds.to_array(dim='band')


# Reorder the dimensions to ('time', 'band', 'x', 'y')
band_dataarray = band_dataarray.transpose('time', 'band', 'x', 'y')
band_dataarray

<xarray.DataArray (time: 142, band: 3, x: 10, y: 10)> Size: 85kB
array([[[[ 5348,  5376,  5400, ...,  5316,  5376,  5468],
         [ 5384,  5364,  5396, ...,  5324,  5348,  5488],
         [ 5460,  5456,  5416, ...,  5376,  5424,  5468],
         ...,
         [ 5496,  5500,  5488, ...,  5444,  5444,  5540],
         [ 5500,  5500,  5496, ...,  5464,  5508,  5540],
         [ 5508,  5528,  5520, ...,  5528,  5544,  5508]],

        [[ 5420,  5376,  5308, ...,  5460,  5536,  5624],
         [ 5408,  5344,  5304, ...,  5472,  5584,  5624],
         [ 5368,  5312,  5284, ...,  5488,  5508,  5604],
         ...,
         [ 5476,  5436,  5376, ...,  5532,  5588,  5612],
         [ 5424,  5428,  5424, ...,  5552,  5644,  5720],
         [ 5388,  5428,  5400, ...,  5596,  5628,  5664]],

        [[ 5396,  5384,  5416, ...,  5796,  5836,  5832],
         [ 5408,  5416,  5516, ...,  5748,  5796,  5852],
         [ 5416,  5416,  5472, ...,  5772,  5804,  5828],
         ...,
...
         ...,
         [ 9240,  9288,  9296, ...,  9304,  9336,  9400],
         [ 9128,  9272,  9256, ...,  9352,  9400,  9376],
         [ 9152,  9280,  9248, ...,  9312,  9368,  9424]],

        [[ 9528,  9600,  9624, ...,  9696,  9680,  9584],
         [ 9544,  9584,  9656, ...,  9584,  9656,  9680],
         [ 9584,  9616,  9592, ...,  9672,  9680,  9696],
         ...,
         [ 9600,  9592,  9616, ...,  9800,  9752,  9752],
         [ 9712,  9672,  9624, ...,  9776,  9792,  9824],
         [ 9656,  9600,  9672, ...,  9800,  9760,  9744]],

        [[10192, 10168, 10192, ..., 10176, 10048, 10136],
         [10232, 10216, 10272, ..., 10136, 10136, 10088],
         [10208, 10192, 10248, ..., 10224, 10232, 10152],
         ...,
         [10240, 10200, 10288, ..., 10240, 10256, 10328],
         [10256, 10216, 10376, ..., 10280, 10352, 10328],
         [10208, 10240, 10304, ..., 10320, 10352, 10264]]]], dtype=uint16)
Coordinates:
  * y        (y) float64 80B 2.53e+06 2.529e+06 ... 2.529e+06 2.529e+06
  * x        (x) float64 80B 3.762e+06 3.762e+06 ... 3.762e+06 3.762e+06
  * time     (time) datetime64[ns] 1kB 2023-01-02T10:44:41.025000 ... 2023-12...
  * band     (band) object 24B 'B04' 'B03' 'B02'

In [25]:
gif_img = geogif.gif(band_dataarray, fps=8)#.compute()
gif_img

In [3]:
#toto = xr.open_dataarray("/eos/jeodpp/home/users/osekenj/data/temp_data/test08/S2_fid-0_patch_2023-01-01 00:00:00-2023-12-31 00:00:00.nc", engine="netcdf4")

toto_gif = export.export2gif(toto.B02, imgfile="/eos/jeodpp/home/users/osekenj/data/temp_data/test08/toto.gif", fps=8, bytes=False, robust=False)
toto_gif

AttributeError: module 'matplotlib.cm' has no attribute 'get_cmap'